In [1]:
# %% Config for SINGLE-TURN validation (DeepSeek)
import validation_library as veri
import os
import importlib

# Where the single-turn synthesis lives:
results_json = "reports/isolated/DeepSeek/contracts_PVP_single.json"

# Where to write validation outputs:
results_csv = "reports/isolated/validation_results_DeepSeek_single.csv"
patches_dir = "reports/isolated/DeepSeek/patches_DeepSeek_single/"

# (Optional) a “fixed” CSV if you later post-process rows
fixed_results_csv = "reports/isolated/validation_results_DeepSeek_single_fixed.csv"


In [2]:
# %% Prepare benchmark contracts (SmartBugs 0.4.x) and strip report markers
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

importlib.reload(veri)

counter_greater_than_200 = 0
contract_lines_4X = []

contracts_4X = veri.get_files("smartbugs-curated/0.4.x/contracts/dataset")

for contract_path, contract_name in contracts_4X:
    contract, line = veri.find_occurrences(contract_path, "// <yes> <report>")
    if contract.count('\n') > 200:
        counter_greater_than_200 += 1 
    else:
        clean_contract = veri.replace_lines_with_string(contract, line, '')
        contract_lines_4X.append((contract_name, clean_contract, line))

# Save under isolated/ to keep outputs tidy
veri.print_json_report("reports/isolated/contract_no_comment.json", contract_lines_4X)
veri.print_txt_report("reports/isolated/contract_no_comment.txt", contract_lines_4X)


In [3]:
# %% Load artifacts (single-turn synthesis + contracts)
importlib.reload(veri)

contracts_with_results = veri.read_json_report(results_json)
contract_lines = veri.read_json_report("reports/isolated/contract_no_comment.json")


In [5]:
# %% Validate single-turn guards across strategies, write CSV and patches
from tqdm import tqdm
import os
import re
import importlib
importlib.reload(veri)

# Make sure outputs exist
os.makedirs(os.path.dirname(results_csv), exist_ok=True)
os.makedirs(patches_dir, exist_ok=True)

headers = [
    'Solidity_file_name',
    'vulnerability_type',
    'vulnerable_line_number',
    'vulnerability_function_entry_line',
    'vulnerability_function_end_line',
    'VL',
    'pre_post',
    'pre',
    'post',
    'pre_VL_post',
    'pre_VL',
    'VL_post'
]

# Loop contracts from the SmartBugs set
for contract in tqdm(contract_lines, desc="Processing contracts"):
    contract_name = contract[0]        # filename relative to smartbugs repo
    contract_code = contract[1]        # stripped source
    lines = contract[2]                # marker line(s), not used directly below

    # Each synthesis entry for this contract name (from your JSON)
    for contract_patch_VL in tqdm(contracts_with_results.get(contract[0], []),
                                  desc=f"Patches for {contract_name}", leave=False):
        # The JSON structure: (full_contract_text, {"VL":(line, req), "pre":(line, req), "post":(line, req)})
        contract_patch_text = contract_patch_VL[0]
        VL_line, VL_require = contract_patch_VL[1]["VL"]
        pre_line, pre_require = contract_patch_VL[1]["pre"]
        post_line, post_require = contract_patch_VL[1]["post"]

        print(f"******* {contract_name}")
        print(f">>>>>>> pre   {pre_line}: {pre_require}")
        print(f">>>>>>> VL    {VL_line}: {VL_require}")
        print(f">>>>>>> post  {post_line}: {post_require}")
        print(" - " * 40)

        # --- VL only ---
        contract_patch = veri.replace_lines_with_string(contract_patch_text, [VL_line], VL_require)
        patch_VL = (contract_patch, VL_line, VL_require)
        no_test, result_VL = veri.evaluate_contracts(contract, patch_VL)
        if no_test:
            break  # skip if test not found

        # --- pre only ---
        contract_patch_pre = veri.insert_empty_line(contract_code, pre_line)
        contract_patch_pre = veri.replace_lines_with_string(contract_patch_pre, [pre_line], pre_require)
        patch_pre = (contract_patch_pre, pre_line, pre_require)
        _, result_pre = veri.evaluate_contracts(contract, patch_pre)

        # --- post only ---
        contract_patch_post = veri.insert_empty_line(contract_code, post_line)
        contract_patch_post = veri.replace_lines_with_string(contract_patch_post, [post_line], post_require)
        patch_post = (contract_patch_post, post_line, post_require)
        _, result_post = veri.evaluate_contracts(contract, patch_post)

        # --- pre + post ---
        contract_patch_pre_post = veri.insert_empty_line(contract_code, post_line)
        contract_patch_pre_post = veri.replace_lines_with_string(contract_patch_pre_post, [post_line], post_require)
        contract_patch_pre_post = veri.insert_empty_line(contract_patch_pre_post, pre_line)
        contract_patch_pre_post = veri.replace_lines_with_string(contract_patch_pre_post, [pre_line], pre_require)
        patch_lines = f"{pre_line},{post_line}"
        PP_require = f"{pre_require},{post_require}"
        patch_pre_post = (contract_patch_pre_post, patch_lines, PP_require)
        _, result_pre_post = veri.evaluate_contracts(contract, patch_pre_post)

        # --- pre + VL + post (PVP) ---
        contract_patch_PVP = veri.insert_empty_line(contract_patch, post_line)
        contract_patch_PVP = veri.replace_lines_with_string(contract_patch_PVP, [post_line], post_require)
        contract_patch_PVP = veri.insert_empty_line(contract_patch_PVP, pre_line)
        contract_patch_PVP = veri.replace_lines_with_string(contract_patch_PVP, [pre_line], pre_require)
        patch_lines = f"{pre_line},{VL_line},{post_line}"
        PVP_require = f"{pre_require},{VL_require},{post_require}"
        patch_PVP = (contract_patch_PVP, patch_lines, PVP_require)
        _, result_PVP = veri.evaluate_contracts(contract, patch_PVP)

        # --- pre + VL (PV) ---
        contract_patch_PV = veri.insert_empty_line(contract_patch, pre_line)
        contract_patch_PV = veri.replace_lines_with_string(contract_patch_PV, [pre_line], pre_require)
        patch_lines = f"{pre_line},{VL_line}"
        PV_require = f"{pre_require},{VL_require}"
        patch_PV = (contract_patch_PV, patch_lines, PV_require)
        _, result_PV = veri.evaluate_contracts(contract, patch_PV)

        # --- VL + post (VP) ---
        contract_patch_VP = veri.insert_empty_line(contract_patch, post_line)
        contract_patch_VP = veri.replace_lines_with_string(contract_patch_VP, [post_line], post_require)
        patch_lines = f"{VL_line},{post_line}"
        VP_require = f"{VL_require},{post_require}"
        patch_VP = (contract_patch_VP, patch_lines, VP_require)
        _, result_VP = veri.evaluate_contracts(contract, patch_VP)

        # Vulnerability label (same helper)
        type_V = veri.get_directory_name(contract_name, "sb-heists/smartbugs-curated")

        # Append row to CSV (same schema)
        row = {
            'Solidity_file_name': contract_name,
            'vulnerability_type': type_V,
            'vulnerable_line_number': VL_line,
            'vulnerability_function_entry_line': pre_line - 1,
            'vulnerability_function_end_line': post_line,
            'VL': result_VL,
            'pre_post': result_pre_post,
            'pre': result_pre,
            'post': result_post,
            'pre_VL_post': result_PVP,
            'pre_VL': result_PV,
            'VL_post': result_VP
        }
        veri.append_row(results_csv, headers, row)

        # Save per-strategy patched sources (for inspection/reproduction)
        strategy_patch_map = {
            'VL': contract_patch,
            'pre': contract_patch_pre,
            'post': contract_patch_post,
            'pre_post': contract_patch_pre_post,
            'pre_VL_post': contract_patch_PVP,
            'pre_VL': contract_patch_PV,
            'VL_post': contract_patch_VP
        }
        veri.save_patches_by_strategy(
            output_dir=patches_dir,
            contract_name=contract_name,
            strategy_patch_map=strategy_patch_map
        )


Processing contracts:   0%|          | 0/131 [00:00<?, ?it/s]

******* random_number_generator.sol
>>>>>>> pre   11: require(salt == 0);
>>>>>>> VL    11: require(max > 0);
>>>>>>> post  26: require(msg.sender == address(this));
 -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  - 


Processing contracts:   2%|▏         | 2/131 [00:00<00:37,  3.48it/s]

******* lottery.sol
>>>>>>> pre   35: require(msg.value > 0);
>>>>>>> VL    37: require(msg.value > 0);
>>>>>>> post  51: require(msg.sender == organizer);
 -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  - 


******* old_blockhash.sol
>>>>>>> pre   33: require(guesses[msg.sender].block != 0);
>>>>>>> VL    34: require(answer != 0);
>>>>>>> post  41: require(block.number > guesses[msg.sender].block);
 -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  - 

=== Evaluating patches for contract: old_blockhash.sol ===

[Patch on line 34] Evaluation Results:
Inserted Require: require(answer != 0);
Results for this run: 
Loading patch from /Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/evaluation_results/old_blockhash.sol_patch_line_34.sol while the contract_file is: /Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/smartbugs-curated/0.4.x/contracts/dataset/bad_randomness/old_blockhash.sol and the main_contract is: old_blockhash.sol
Initializing patch evaluator
Base directory: ../smartbugs-curated/0.4.x
Executing command:  npx hardhat compile
Now using node v22.19.0 (npm v10.9.3)
Compiled 1 Solidity f

...

Processing contracts:  99%|█████████▉| 130/131 [1:12:16<00:33, 33.02s/it]

******* governmental_survey.sol
>>>>>>> pre   23: require(msg.value >= jackpot / 2);
>>>>>>> VL    26: require(msg.sender == lastInvestor);
>>>>>>> post  28: require(msg.value >= jackpot / 2);
 -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  - 


******* timed_crowdsale.sol
>>>>>>> pre   12: require(block.timestamp >= 1546300800);
>>>>>>> VL    12: require(block.timestamp >= 1546300800);
>>>>>>> post  14: require(block.timestamp >= 1546300800);
 -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  -  - 

=== Evaluating patches for contract: timed_crowdsale.sol ===

[Patch on line 12] Evaluation Results:
Inserted Require: require(block.timestamp >= 1546300800);
Results for this run: 
Loading patch from /Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/evaluation_results/timed_crowdsale.sol_patch_line_12.sol while the contract_file is: /Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/smartbugs-curated/0.4.x/contracts/dataset/time_manipulation/timed_crowdsale.sol and the main_contract is: timed_crowdsale.sol
Initializing patch evaluator
Base directory: ../smartbugs-curated/0.4.x
Executing command:  npx hardhat compile
Now using node v22.19.

Processing contracts: 100%|██████████| 131/131 [1:13:02<00:00, 33.46s/it]


[Patch on line 12,14] Evaluation Results:
Inserted Require: require(block.timestamp >= 1546300800);,require(block.timestamp >= 1546300800);
Results for this run: 
Loading patch from /Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/evaluation_results/timed_crowdsale.sol_patch_line_12,14.sol while the contract_file is: /Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/smartbugs-curated/0.4.x/contracts/dataset/time_manipulation/timed_crowdsale.sol and the main_contract is: timed_crowdsale.sol
Initializing patch evaluator
Base directory: ../smartbugs-curated/0.4.x
Executing command:  npx hardhat compile
Now using node v22.19.0 (npm v10.9.3)
Compiled 1 Solidity file successfully (evm target: unknown evm version for solc version 0.4.25).


Starting patch evaluation
The actual patch is: Patch(path='/Users/mojtabae/projects/FLAMES/raw-validation-results/sb-heists/evaluation_results/timed_crowdsale.sol_patch_line_12,14.sol', contract_file='/Users/mojtabae/project